# **Import of libraries**



In [ ]:
%tensorflow_version 2.x

Colab only includes TensorFlow 2.x; %tensorflow_version has no effect.


In [ ]:
!pip install SpeechRecognition # библиотека с популярными сервисами распознавания речи
import speech_recognition as sR
!pip install jiwer
from jiwer import wer # модуль метрики качества в распознавании речи
import numpy as np # библиотека для работы с массивами данных
from matplotlib import pyplot as plt # интерфейс для построения графиков простых функций
from IPython.display import HTML, Audio # загружаем модуль чтобы обратиться к HTML для записи аудио с микрофона в ноутбуке
from google.colab import files # модуль для загрузки файлов
from google.colab.output import eval_js
from base64 import b64decode # модуль для кодировки/раскодировки аудиозаписи(64-разрядный код)
from scipy.io.wavfile import read as wav_read # для чтения WAV формата
import io
import scipy # воспользуемся модулями библиотеки для работы со звуковой дорожкой
import librosa # для параметризации аудио
import os # модуль для работы с операционной системой(воспользуемся методами работы с каталогами)
from sklearn.model_selection import train_test_split # модуль для разбивки данных на обучающую и тестовую выборки
from keras.utils import to_categorical # загружаем утилиты кераса для one hot кодировки
from tqdm import tqdm # быстрый, удобный progress bar для Python
from keras.optimizers import Adam, RMSprop, Adadelta # загружаем алгоритмы обучения/оптимизации
from keras.models import Sequential # последовательная модель нейросети кераса
from keras.layers import Dense, Dropout, Flatten, Conv2D, MaxPooling2D, BatchNormalization # загружаем необходимые слои для нейросети
import IPython.display as ipd #Для проигрывания аудио

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 32.9/32.9 MB 57.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 48.5 MB/s eta 0:00:00


In [ ]:
from google.colab import drive # подключаем гугл драйв диск для загрузки файлов
drive.mount('/content/drive')

# ** Example of recognition with google api**




In [ ]:
##########################
# Зададим функцию распознавания аудио с помощью speech_recognition
##########################
def recognizeAudio(filename, duration=None):
  AUDIO_FILE = os.path.join(filename) # задаем путь к аудиофайлу
  r = sR.Recognizer() # создаем объект класса Recognizer
  with sR.AudioFile(AUDIO_FILE) as source:
    audio = r.record(source, duration=duration) # считываем аудиофайл

  return r.recognize_google(audio, language='ru') # запускаем распознавание

In [ ]:
# Распознавание на примере короткой фразы без шумов на заднем плане
team_path_gde = '/content/drive/My Drive/Аудио для Speech recognition/где мы встретимся.wav'
# Распознавание на примере длинной фразы без шумов на заднем плане
team_path_wilhelm = '/content/drive/My Drive/Аудио для Speech recognition/Sample.wav'
# Распознавание отрезка из видео на ютубе с негромкой фоновой музыкой
team_path_anews = '/content/drive/My Drive/Аудио для Speech recognition/аудио_видос_короткий.wav'
# Распознавание отрезка из песни с четкой речью
team_path_splin = '/content/drive/My Drive/Аудио для Speech recognition/Сплин_Романс.wav'
# Распознавание отрезка из песни с менее четкой речью и более зашумленной
team_path_uvarova = '/content/drive/My Drive/Аудио для Speech recognition/Аня Уварова_Улыбка.wav'
# Распознавание отрывка из интервью
team_path_interview = '/content/drive/My Drive/Аудио для Speech recognition/интервью.wav'
# Распознавание отрывка из политических дебатов (транскрипт здесь даже вручную сделать непросто, так как голоса накладываются друг на друга,
# поэтому для подсчета WER будем учитывать только те слова, которые слышно лучше)
team_path_debaty = '/content/drive/My Drive/Аудио для Speech recognition/дебаты шумные.wav'


In [ ]:
# Простая фраза
ipd.display(ipd.Audio(team_path_gde))

In [ ]:
original = 'где мы встретимся'
res = recognizeAudio(team_path_gde)

print('Оригинал:               ', original)
print('Результат распознавания:', res)
print('WER:', wer(original.lower(), res.lower())) # считаем метрику качества

Оригинал:                где мы встретимся
Результат распознавания: Где мы встретимся
WER: 0.0


In [ ]:
# client_path_wilhelm = '/content/drive/My Drive/Аудио для Speech recognition/Sample.wav'
original = 'Вильгельм гауф карлик нос господин совсем не правы люди думающие что феи и волшебники существовали только во времена гаруна аль рашида властелина багдада или даже утверждающие что те повествования о деятельности духов и их повелителей которые слышишь от рассказчиков на городских рынках неверны феи существуют еще и теперь не так давно я сам был свидетелем одного происшествия в котором явно участвовали духи как я вам расскажу много лет тому назад в одном значительном городе моего милого отечества Германии скромно и честно жил сапожник с женой днём Он сидел на углу улицы и чинил башмаки и туфли делал он может быть и новые если это кто-нибудь доверял ему но в таком случае он должен был сперва купить кожу так как был беден и не имел запасов его жена продавала овощи и фрукты которые разводила в маленьком садике за городом и многие охотно покупали у неё потому что она была чисто и опрятно одета и умела красиво разложить и выставить свой товар у них был красивый мальчик приятный лицом хорошо сложенный и для своего восьмилетнего возраста уже довольно большой он обыкновенно сидел около матери на овощном рынке относил также домой часть плодов тем женщинам или поварам которые много закупали у жены сапожника и редко возвращался с такой прогулки без красивого цветка монетки или пирога Потому что господам этих поваров было приятно видеть когда приводили в дом красивого мальчика и они всегда щедро одаривали его однажды жена сапожника по обыкновению опять сидела на рынке перед ней было несколько корзин с капустой и другими овощами разные травы и семена а также в корзиночке поменьше ранние груши яблоки и абрикосы маленький Якоб'
res = recognizeAudio(team_path_wilhelm, duration=120) # на больших файлах желательно указывать длительность, чтобы избежать ошибки распознавания

print('Оригинал:               ', original)
print('Результат распознавания:', res)
print('WER:', wer(original.lower(), res.lower()))

Оригинал:                Вильгельм гауф карлик нос господин совсем не правы люди думающие что феи и волшебники существовали только во времена гаруна аль рашида властелина багдада или даже утверждающие что те повествования о деятельности духов и их повелителей которые слышишь от рассказчиков на городских рынках неверны феи существуют еще и теперь не так давно я сам был свидетелем одного происшествия в котором явно участвовали духи как я вам расскажу много лет тому назад в одном значительном городе моего милого отечества Германии скромно и честно жил сапожник с женой днём Он сидел на углу улицы и чинил башмаки и туфли делал он может быть и новые если это кто-нибудь доверял ему но в таком случае он должен был сперва купить кожу так как был беден и не имел запасов его жена продавала овощи и фрукты которые разводила в маленьком садике за городом и многие охотно покупали у неё потому что она была чисто и опрятно одета и умела красиво разложить и выставить свой товар у них был красивый мальчи

In [ ]:
# Пример речи с фоновой музыкой
ipd.display(ipd.Audio(team_path_anews))

In [ ]:
original = 'anews.ru первое устройство для распознавания речи появилось в 1952 году оно могло понимать произнесённые человеком цифры 40 лет спустя были представлены первые коммерческие программы распознающие речь человека они были предназначены для людей которые в силу физиологических особенностей не могли набирать текст вручную сейчас же функция распознавания речи есть практически в любом смартфоне Она позволяет нам взаимодействовать голосом с приложениями облегчая и упрощая нашу жизнь как же работает распознавание речи об этом в сегодняшнем выпуске'
res = recognizeAudio(team_path_anews)

print('Оригинал:               ', original)
print('Результат распознавания:', res)
print('WER:', wer(original.lower(), res.lower()))

Оригинал:                anews.ru первое устройство для распознавания речи появилось в 1952 году оно могло понимать произнесённые человеком цифры 40 лет спустя были представлены первые коммерческие программы распознающие речь человека они были предназначены для людей которые в силу физиологических особенностей не могли набирать текст вручную сейчас же функция распознавания речи есть практически в любом смартфоне Она позволяет нам взаимодействовать голосом с приложениями облегчая и упрощая нашу жизнь как же работает распознавание речи об этом в сегодняшнем выпуске
Результат распознавания: ru первое устройство для распознавания речи появилось в 1952 году она могло понимать произнесённые человеком цифры 40 лет спустя были представлены первые коммерческие программы распознающая речь человека они были предназначены для людей которые в силу физиологических особенностей не могли набирать текст вручную сейчас же функция распознавания речи есть практически в любом смартфоне Она позволяет нам вз

In [ ]:
# Пример песни Сплин - Романс
ipd.display(ipd.Audio(team_path_splin))

In [ ]:
# client_path_splin = '/content/drive/My Drive/Аудио для Speech recognition/Сплин_Романс.wav'
original = 'и лампа не горит и врут календари и если ты давно хотела что то мне сказать то говори любой обманчив звук страшнее тишина когда в самый разгар веселья падает из рук бокал вина и черный кабинет и ждет в стволе патрон так тихо что я слышу как идет на глубине вагон метро на площади полки темно в конце строки и в телефонной трубке эти много лет спустя одни гудки и где то хлопнет дверь и дрогнут провода привет мы будем счастливы теперь и навсегда привет мы будем счастливы теперь и навсегда'
res = recognizeAudio(team_path_splin, duration=120)

print('Оригинал:               ', original)
print('Результат распознавания:', res)
print('WER:', wer(original.lower(), res.lower()))

Оригинал:                и лампа не горит и врут календари и если ты давно хотела что то мне сказать то говори любой обманчив звук страшнее тишина когда в самый разгар веселья падает из рук бокал вина и черный кабинет и ждет в стволе патрон так тихо что я слышу как идет на глубине вагон метро на площади полки темно в конце строки и в телефонной трубке эти много лет спустя одни гудки и где то хлопнет дверь и дрогнут провода привет мы будем счастливы теперь и навсегда привет мы будем счастливы теперь и навсегда
Результат распознавания: и лампа не горит и врут календари и если ты давно хотела что-то мне сказать Он говорит любой обманчив звук страшнее тишина Когда в самый разгар веселья и Чёрный кабинет и ждёт в стволе патрон Так тихо что я слышу
WER: 0.6153846153846154


In [ ]:
# Пример песни Аня Уварова - Улыбка (многоголосье во втором припеве)
ipd.display(ipd.Audio(team_path_uvarova))

In [ ]:
# client_path_uvarova =  '/content/drive/My Drive/Аудио для Speech recognition/Аня Уварова_Улыбка.wav'
original = 'от улыбки хмурый день светлей от улыбки в небе радуга проснется поделись улыбкою своей и она к тебе не раз еще вернется и тогда наверняка вдруг запляшут облака и кузнечик запиликает на скрипке с голубого ручейка начинается река ну а дружба начинается с улыбки с голубого ручейка начинается река ну а дружба начинается с улыбки от улыбки солнечной одной перестанет плакать самый грустный дождик сонный лес простится с тишиной и захлопает в зеленые ладоши и тогда наверняка вдруг запляшут облака и кузнечик запиликает на скрипке с голубого ручейка начинается река ну а дружба начинается с улыбки с голубого ручейка начинается река ну а дружба начинается с улыбки от улыбки станет всем теплей и слону и даже маленькой улитке так пускай повсюду на земле будто лампочки включаются улыбки и тогда наверняка вдруг запляшут облака и кузнечик запиликает на скрипке с голубого ручейка начинается река ну а дружба начинается с улыбки с голубого ручейка начинается река ну а дружба начинается с улыбки'
res = recognizeAudio(team_path_uvarova, duration=90)

print('Оригинал:               ', original)
print('Результат распознавания:', res)
print('WER:', wer(original.lower(), res.lower()))

Оригинал:                от улыбки хмурый день светлей от улыбки в небе радуга проснется поделись улыбкою своей и она к тебе не раз еще вернется и тогда наверняка вдруг запляшут облака и кузнечик запиликает на скрипке с голубого ручейка начинается река ну а дружба начинается с улыбки с голубого ручейка начинается река ну а дружба начинается с улыбки от улыбки солнечной одной перестанет плакать самый грустный дождик сонный лес простится с тишиной и захлопает в зеленые ладоши и тогда наверняка вдруг запляшут облака и кузнечик запиликает на скрипке с голубого ручейка начинается река ну а дружба начинается с улыбки с голубого ручейка начинается река ну а дружба начинается с улыбки от улыбки станет всем теплей и слону и даже маленькой улитке так пускай повсюду на земле будто лампочки включаются улыбки и тогда наверняка вдруг запляшут облака и кузнечик запиликает на скрипке с голубого ручейка начинается река ну а дружба начинается с улыбки с голубого ручейка начинается река ну а дружба начин

In [ ]:
# Пример речи из интервью
ipd.display(ipd.Audio(team_path_interview))

In [ ]:
# client_path_interview = '/content/drive/My Drive/Аудио для Speech recognition/интервью.wav'
original = 'добрый день коллеги сегодня у нас в гостях человек которого вы надеюсь узнаете Это Александр Геннадьевич Дьяконов Надеюсь вы его знаете по соревнованиям кэггл либо Вы у него учились в МГУ это профессор вмк МГУ занимается машинным обучением давайте я в первую очередь спрошу Ну вот мы вас скорее всего знаем по соревнованиям кэггл вы один из первых успешных отечественных участников это платформа соревнований Скажите вот мы за вами следили Может быть сейчас не все знают чем вы занимаетесь какие проекты ведёте Связаны ли они с data science или может быть там вы уже в квантовые вычисления куда-то ушли то есть вы хотите successful стори есть ли жизнь после кэггла Да нет всё скажем так загадочно и неизвестно то есть у меня сейчас некая ну скажем так кризис среднего возраста некие изменения там в профессиональной сфере и в том числе возможно я поменяю там и род деятельности и место работы и так далее я сейчас пока подробно об этом не буду но есть такая большая вероятность вот Ну кроме того большие изменения в личной жизни там у меня ребёнок появился поэтому там свободного времени для того же кэггла естесственно нету вот а так всё по-прежнему Я преподаю в Московском университете сейчас очень много прикладных проектов то есть решают кучу задач вот в последние две недели на самом деле я там программировал в очень жестком режиме то есть приходилось там доделывать один проект вот так что всё Так буднично банально ничего интересного хорошо Да а вот Наверное в основном люди представляют что вы именно Эксперт в соревнованиях кэггл вот по поводу кэггла у меня может быть даже не вопрос или это такой развернутый вопрос или это вообще наброс но бытует мнение что конечно при всех достоинствах соревнования'
res = recognizeAudio(team_path_interview)

print('Оригинал:               ', original)
print('Результат распознавания:', res)
print('WER:', wer(original.lower(), res.lower()))

Оригинал:                добрый день коллеги сегодня у нас в гостях человек которого вы надеюсь узнаете Это Александр Геннадьевич Дьяконов Надеюсь вы его знаете по соревнованиям кэггл либо Вы у него учились в МГУ это профессор вмк МГУ занимается машинным обучением давайте я в первую очередь спрошу Ну вот мы вас скорее всего знаем по соревнованиям кэггл вы один из первых успешных отечественных участников это платформа соревнований Скажите вот мы за вами следили Может быть сейчас не все знают чем вы занимаетесь какие проекты ведёте Связаны ли они с data science или может быть там вы уже в квантовые вычисления куда-то ушли то есть вы хотите successful стори есть ли жизнь после кэггла Да нет всё скажем так загадочно и неизвестно то есть у меня сейчас некая ну скажем так кризис среднего возраста некие изменения там в профессиональной сфере и в том числе возможно я поменяю там и род деятельности и место работы и так далее я сейчас пока подробно об этом не буду но есть такая большая вероятнос

In [ ]:
# Пример речи с дебатов
ipd.display(ipd.Audio(team_path_debaty))

In [ ]:
# client_path_debaty = '/content/drive/My Drive/Аудио для Speech recognition/дебаты шумные.wav'
original = "совершенный беспредел совершенный там цены останавливаются произвольно вся экономика современной обороны и оборонной промышленности России лежит в разрухе григорий алексеевич и поедает все основные доходы кто пришел к власти в 91 году которые есть дорога есть вот я хотел американский явлинский чубайс гайдар вы пришли вы разворовали вот я вам могу сказать вы участники что я вы провели все эти реформы дурацкие хотел я хотел и сидите на поводке да у спецслужб запада значит я хотел бы подчеркнуть хотел бы подчеркнуть хватит говорить поскольку у меня поскольку остается 30 секунд у нас дебаты здесь то я хотел бы сказать на дебатах а не чтобы слушать маразм следующее 3 соображения на дебатах да лучше защищать предпринимателей чем пули это вам точнее второе что я очень важное хотел сказать что Сталин убийца Кровавый это вранье убийца это правда людей а жириновский дешевый лжец межнациональные конфликты при таком иконостасе страна не имеет перспективы только грязь можете и нашу родину спокойно ну прекратите уже в самом деле ну что ж это такое во-первых"
res = recognizeAudio(team_path_debaty, duration=50)

print('Оригинал:               ', original)
print('Результат распознавания:', res)
print('WER:', wer(original.lower(), res.lower()))

Оригинал:                совершенный беспредел совершенный там цены останавливаются произвольно вся экономика современной обороны и оборонной промышленности России лежит в разрухе григорий алексеевич и поедает все основные доходы кто пришел к власти в 91 году которые есть дорога есть вот я хотел американский явлинский чубайс гайдар вы пришли вы разворовали вот я вам могу сказать вы участники что я вы провели все эти реформы дурацкие хотел я хотел и сидите на поводке да у спецслужб запада значит я хотел бы подчеркнуть хотел бы подчеркнуть хватит говорить поскольку у меня поскольку остается 30 секунд у нас дебаты здесь то я хотел бы сказать на дебатах а не чтобы слушать маразм следующее 3 соображения на дебатах да лучше защищать предпринимателей чем пули это вам точнее второе что я очень важное хотел сказать что Сталин убийца Кровавый это вранье убийца это правда людей а жириновский дешевый лжец межнациональные конфликты при таком иконостасе страна не имеет перспективы только грязь может